In [1]:
import numpy as np
import pandas as pd
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, precision_score,recall_score
from sklearn.svm import LinearSVC
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
import keras
from keras import layers
from keras.models import Sequential, load_model
from keras.layers import Dense, Activation, Flatten
from keras.layers import LSTM
from keras.optimizers import RMSprop
from keras.utils.data_utils import get_file
from keras.callbacks import EarlyStopping
from keras.layers import Embedding
from keras.preprocessing import text
import string
import nltk
import re



In [2]:
nltk.download("stopwords")

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\beth\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

# Data Preprocess

In [3]:
df1 = pd.read_csv("PATIENTS.csv", delimiter=',', skipinitialspace=True, header=0)

df1.columns = ["Subject_Id", "Expire_label"]

df1.head()





Subject_Id  Expire_label
0           2             0
1           3             1
2           4             0
3           5             0
4           6             0

In [4]:

df2=pd.read_csv("NOTEEVENTS.csv", delimiter=',', skipinitialspace=True, header=0)

df2.head()

df2.columns = ["Row_id", "Subject_Id", "HADM_id", "Chartdate", 'charttime', 'storetime', 'category', 'description', 'cgid', 'iserror', 'Text']

df2.head()


c:\users\beth\anaconda3\envs\tf-gpu\lib\site-packages\IPython\core\interactiveshell.py:3166: DtypeWarning: Columns (4,5) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


Row_id  Subject_Id   HADM_id   Chartdate charttime storetime  \
0     174       22532  167853.0  2151-08-04       NaN       NaN   
1     175       13702  107527.0  2118-06-14       NaN       NaN   
2     176       13702  167118.0  2119-05-25       NaN       NaN   
3     177       13702  196489.0  2124-08-18       NaN       NaN   
4     178       26880  135453.0  2162-03-25       NaN       NaN   

            category description  cgid  iserror  \
0  Discharge summary      Report   NaN      NaN   
1  Discharge summary      Report   NaN      NaN   
2  Discharge summary      Report   NaN      NaN   
3  Discharge summary      Report   NaN      NaN   
4  Discharge summary      Report   NaN      NaN   

                                                Text  
0  Admission Date:  [**2151-7-16**]       Dischar...  
1  Admission Date:  [**2118-6-2**]       Discharg...  
2  Admission Date:  [**2119-5-4**]              D...  
3  Admission Date:  [**2124-7-21**]              ...  
4  Admission Date:  [**2162-3-3**]              D...

In [5]:
df2=df2.drop(columns=['Row_id', 'HADM_id', 'Chartdate', 'charttime', 'storetime', 'category', 'description', 'cgid', 'iserror'])


df2.head()

Subject_Id                                               Text
0       22532  Admission Date:  [**2151-7-16**]       Dischar...
1       13702  Admission Date:  [**2118-6-2**]       Discharg...
2       13702  Admission Date:  [**2119-5-4**]              D...
3       13702  Admission Date:  [**2124-7-21**]              ...
4       26880  Admission Date:  [**2162-3-3**]              D...

In [6]:
df=pd.merge(df1, df2, on='Subject_Id')

df.head()

Subject_Id  Expire_label                                               Text
0           2             0  Nursing Transfer note\n\n\nPt admitted to NICU...
1           2             0  Neonatology Attending Triage Note\n\nBaby [**N...
2           3             1  Admission Date:  [**2101-10-20**]     Discharg...
3           3             1  PATIENT/TEST INFORMATION:\nIndication: S/P Car...
4           3             1  PATIENT/TEST INFORMATION:\nIndication: Pericar...

In [7]:
df.shape

(2083180, 3)

In [8]:
from sklearn.utils import shuffle
df = shuffle(df)

df.head()

Subject_Id  Expire_label  \
416480         9122             0   
515100        11332             1   
1196352       26771             0   
1971671       89294             0   
58471          1193             1   

                                                      Text  
416480   [** **] Attending\n\nDay 54\n\nRemains on nasa...  
515100   Patient treated with albuterol and Atrovent vi...  
1196352  Chief Complaint: cholangitis\n   I saw and exa...  
1971671  76 year old female redo mvr , allergies to pcn...  
58471    ADDENDUM TO NPN:\nTrach care done and pt noted...

In [9]:
df=df.drop(df.index[0:1983180])
print(df)

df.to_csv('data.csv')

         Subject_Id  Expire_label  \
484985        10653             1   
849997        18946             0   
47153           942             0   
685198        15204             0   
1381971       31082             0   
...             ...           ...   
418418         9169             1   
1198028       26829             1   
286908         6262             0   
621374        13699             0   
677246        15034             0   

                                                      Text  
484985   Sinus rhythm\nFirst degree A-V delay\nProbable...  
849997   Addendum to NPN\nBaby had 1 [**Name2 (NI) **] ...  
47153    Rehab/OT\n\nMet with [** 32**] at the bedside....  
685198   Neonatology Attending\nDay 43, x 28 [**2-3**]\...  
1381971  [**2201-6-25**] 5:28 PM\n CHEST (PRE-OP PA & L...  
...                                                    ...  
418418   Resp Care\nremains intub/vented on ac mode. on...  
1198028  NPN-MICU\nMrs. [**Known lastname 10049**] cont...  
286908

# Remove Stopwords

In [3]:
df=pd.read_csv('data.csv', index_col=0)

df

Subject_Id  Expire_label  \
484985        10653             1   
849997        18946             0   
47153           942             0   
685198        15204             0   
1381971       31082             0   
...             ...           ...   
418418         9169             1   
1198028       26829             1   
286908         6262             0   
621374        13699             0   
677246        15034             0   

                                                      Text  
484985   Sinus rhythm\nFirst degree A-V delay\nProbable...  
849997   Addendum to NPN\nBaby had 1 [**Name2 (NI) **] ...  
47153    Rehab/OT\n\nMet with [** 32**] at the bedside....  
685198   Neonatology Attending\nDay 43, x 28 [**2-3**]\...  
1381971  [**2201-6-25**] 5:28 PM\n CHEST (PRE-OP PA & L...  
...                                                    ...  
418418   Resp Care\nremains intub/vented on ac mode. on...  
1198028  NPN-MICU\nMrs. [**Known lastname 10049**] cont...  
286908   [**2153-1-31**] 3:12 PM\n CHEST (PORTABLE AP);...  
621374   NEURO: PT. ALERT, ANXIOUS IN BEGINNING OF SHIF...  
677246   [**University/College 303**] Pilgrim Nurse Cas...  

[100000 rows x 3 columns]

In [4]:
REPLACE_BY_SPACE_RE = re.compile('[/(){}\[\]\|@,;]')
BAD_SYMBOLS_RE = re.compile('[^0-9a-z #+_]')
STOPWORDS = nltk.corpus.stopwords.words('english')
STOPWORDS.append('Admission')
STOPWORDS.append('Date')
STOPWORDS.append('Discharge')

def clean_text(text):
    text = text.lower()
    text = REPLACE_BY_SPACE_RE.sub(' ', text) 
    text = BAD_SYMBOLS_RE.sub('', text) 
    text = text.replace('x', '')
    text = ' '.join(word for word in text.split() if word not in STOPWORDS) 
    return text

df['Text'] = df['Text'].apply(clean_text)
df['Text'] = df['Text'].str.replace('\d+', '')


df.head()

c:\users\beth\anaconda3\envs\tf-gpu\lib\site-packages\ipykernel_launcher.py:17: FutureWarning: The default value of regex will change from True to False in a future version.


Subject_Id  Expire_label  \
484985        10653             1   
849997        18946             0   
47153           942             0   
685198        15204             0   
1381971       31082             0   

                                                      Text  
484985   sinus rhythmfirst degree av delayprobable left...  
849997   addendum npnbaby  name ni apnea desat feeding ...  
47153    rehab otmet  bedside reviewed care plan develo...  
685198   neonatology attendingday        bs coarse clea...  
1381971    pm chest preop pa lat clip # clip number rad...

In [5]:
df.shape

(100000, 3)